In [ ]:
!pip install -q litellm numpy


In [ ]:
import os
import sys
from typing import List, Dict, Optional
import litellm
import numpy as np
from litellm import completion, embedding

# ===================================================================
# CONFIGURATION
# ===================================================================

def setup_environment() -> str:
    """Safely retrieves the API key from env or user input."""
    api_key = os.getenv("GOOGLE_API_KEY", "")
    if not api_key:
        from getpass import getpass
        print("Credentials missing in environment.")
        api_key = getpass("Enter Google API Key: ")
        os.environ["GOOGLE_API_KEY"] = api_key
    return api_key

# 1. SETUP CREDENTIALS
GOOGLE_API_KEY = setup_environment()

# 2. MODEL SPECIFICATIONS
# 'gemini-1.5-flash' is the optimal cost/performance point.
# Prefix 'gemini/' tells litellm to use the Google AI Studio provider.
model_name = "gemini-2.5-flash"

DEFAULT_MODEL = f"gemini/{model_name}"

EMBEDDING_DIM = 768  # text-embedding-004 produces 768-dimensional vectors


print(f"Targeting Model ID: {DEFAULT_MODEL}")

# ===================================================================
# UTILITIES
# ===================================================================

def test_connection():
    """Simple verification unit to ensure model tags resolve correctly."""
    print(f"\n⚡ Configuration Loaded")
    print(f"   Inference Model : {DEFAULT_MODEL}")
    print(f"   Embedding Model : {EMBEDDING_MODEL} ({EMBEDDING_DIM}d)")

    try:
        # Test Inference
        print("\n1. Testing Generation...", end=" ", flush=True)
        response = completion(
            model=DEFAULT_MODEL,
            messages=[{"role": "user", "content": "Hello, world!"}]
        )
        print("OK.")
        print(f"   Response: {response.choices[0].message.content.strip()}")

        # Test Embedding
        print("2. Testing Embedding...", end=" ", flush=True)
        vec_response = embedding(
            model=EMBEDDING_MODEL,
            input=["Hello, world!"]
        )
        vec = vec_response.data[0]['embedding']
        assert len(vec) == EMBEDDING_DIM, f"Dimension mismatch: got {len(vec)}"
        print("OK.")

    except Exception as e:
        print(f"\n❌ Error: {str(e)}")
        sys.exit(1)

if __name__ == "__main__":
    test_connection()

-*- coding: utf-8 -*-


### Temel Helper Fonksiyon: LLM Çağrısı

Tüm LLM çağrıları için tek bir birleşik arayüz. Model, temperature, max_tokens gibi parametreleri kolayca kontrol edebiliriz.


In [ ]:
def call_llm(
    messages: List[Dict[str, str]],
    model: Optional[str] = DEFAULT_MODEL,
    temperature: float = 0.7,
    max_tokens: int = 1024,
    **kwargs
) -> str:
    if model is None:
        model = DEFAULT_MODEL

    try:
        response = completion(
            model=model,
            messages=messages,
            temperature=temperature,
            max_tokens=max_tokens,
            **kwargs
        )
        return response.choices[0].message.content
    except Exception as e:
        return f"❌ Hata: {str(e)}"

LLM completion için birleşik arayüz.

    Args:
        messages: OpenAI formatında chat mesajları
        model: Model tanımlayıcı (None ise DEFAULT_MODEL kullanılır)
        temperature: Sampling temperature (0.0-1.0)
        max_tokens: Üretilecek maksimum token sayısı

    Returns:
        Model yanıtı


---

## Faz 1: Stokastik Operatör

Şimdi temel stokastik operatörü tanımlıyoruz: Büyük Dil Modeli ve onun prompt mühendisliği ile kontrol mekanizmaları.

### 1.1 LLM Koşullu Dağılım Olarak

Bir LLM, $P(y|x, \theta)$ koşullu olasılık dağılımı olarak görülebilir:
- $x$: girdi promptu (tokenlar)
- $y$: çıktı dizisi (tokenlar)
- $\theta$: model parametreleri (dondurulmuş, önceden eğitilmiş)

$\theta$'yı eğitmiyoruz. Bunun yerine dağılımı şu yollarla manipüle ediyoruz:
1. **Prompt yapısı** (zero-shot, few-shot, chain-of-thought)
2. **Sampling parametreleri** (temperature, top_p)
3. **Bağlam mühendisliği** (system messages, rol atama)

### 1.2 Prompt Mühendisliği Teknikleri

**Zero-Shot Prompting:** Örnek vermeden doğrudan talimat.  
**Few-Shot Prompting:** Format ve mantığı yönlendirmek için örnekler sağlama.  
**Chain-of-Thought (CoT):** Açık adım adım mantık yürütme.


In [ ]:
zero_shot_prompt = "Bu metnin duygusunu analiz et ve sadece tek kelime ile cevap ver: Pozitif, Negatif veya Nötr. Metin: Deniz sakin, lakin dalgalar"

In [ ]:
print(zero_shot_prompt)

In [ ]:
print("="*80)
print("ZERO-SHOT PROMPTING ÖRNEĞİ")
print("="*80)
print(f"\n📝 Prompt:\n{zero_shot_prompt}\n")
print("-"*80)

response = call_llm(
    [{"role": "user", "content": zero_shot_prompt}],
    temperature=0.2,
    max_tokens=50
)

print(f"\n🤖 Model Yanıtı: {response}")
print("\n" + "="*80)



In [ ]:
few_shot_prompt = str("""Şu örneklere bakarak duyguyu sınıflandır:

Metin: Bu telefon harika! Şimdiye kadarki en iyi alışverişim.
Duygu: Pozitif

Metin: Berbat müşteri hizmetleri. Çok hayal kırıklığına uğradım.
Duygu: Negatif

Metin: Ürün zamanında geldi.
Duygu: Nötr

Metin: Tasarımını kesinlikle sevdim ama pil ömrü daha iyi olabilirdi.
Duygu:
""")

print("="*80)
print("FEW-SHOT PROMPTING ÖRNEĞİ")
print("="*80)
print(f"\n📝 Prompt (örneklerle):\n{few_shot_prompt}\n")
print("-"*80)

response = call_llm(
    [{"role": "user", "content": few_shot_prompt}],
    temperature=0.2,
    max_tokens=50
)

print(f"\n🤖 Model Yanıtı: {response}")
print("\n💡 Gözlem: Few-shot, modelin karma duyguları anlamasını sağlar.")
print("="*80)



In [ ]:
cot_prompt = "Bir mağazada bir ürünün fiyatı 80 TL idi. İlk olarak %25 indirim yapıldı, ardından indirimli fiyata %18 KDV eklendi. Ürünün son fiyatı kaç TL'dir? Lütfen adım adım düşünerek cevabı bul."

In [ ]:
print(cot_prompt)

In [ ]:
print("="*80)
print("CHAIN-OF-THOUGHT PROMPTING ÖRNEĞİ")
print("="*80)
print(f"\n📝 Prompt:\n{cot_prompt}\n")
print("-"*80)

response = call_llm(
    [{"role": "user", "content": cot_prompt}],
    temperature=0.0,
    max_tokens=500
)

print(f"\n🤖 Model Yanıtı:\n{response}")
print("\n📐 Doğru Cevap: 80 * 0.75 = 60 TL, sonra 60 * 1.18 = 70.80 TL")
print("\n💡 CoT, karmaşık çok adımlı mantık yürütmeyi mümkün kılar.")
print("="*80)




```
# This is formatted as code
```

### 1.3 Temperature: Stokastiği Kontrol Etme

Temperature $T$, softmax dağılımını değiştirir:

$$P(y_i|x) = \frac{e^{z_i/T}}{\sum_j e^{z_j/T}}$$

- $T \to 0$: Deterministik (argmax)
- $T = 1$: Orijinal dağılım
- $T > 1$: Daha uniform (yaratıcı ama daha az tutarlı)


In [ ]:
creative_prompt = "Bu cümleyi tam 10 kelime ile tamamla: Yapay zekanın geleceği"

print("="*80)
print("TEMPERATURE PARAMETRESİ DENEYİ")
print("="*80)
print(f"\n📝 Prompt: {creative_prompt}\n")
print("="*80)

for temp in [0.0, 0.5, 1.0]:
    print(f"\n🌡️  Temperature = {temp}")
    print("-"*80)

    for i in range(3):
        response = call_llm(
            [{"role": "user", "content": creative_prompt}],
            temperature=temp,
            max_tokens=30
        )
        print(f"   Deneme {i+1}: {response}")

print("\n" + "="*80)
print("\n💡 Gözlemler:")
print("   - T=0.0: Deterministik, her seferinde aynı çıktı")
print("   - T=0.5: Orta derece çeşitlilik, tutarlı kalite")
print("   - T=1.0: Yüksek yaratıcılık, çeşitli çıktılar")
print("="*80)


---

## Faz 2: Semantik Uzay

Şimdi embedding'ler yoluyla semantik uzay oluşturuyor ve Retrieval-Augmented Generation (RAG) uyguluyoruz.

### 2.1 Embeddings: Ayrık Tokenlardan Sürekli Uzaya

Bir embedding fonksiyonu $\phi: \mathcal{V} \to \mathbb{R}^d$ kelime dağarcığını sürekli vektör uzayına eşler:

$$\phi(\text{"kedi"}) \approx \phi(\text{"yavru kedi"}), \quad \phi(\text{"kedi"}) \not\approx \phi(\text{"araba"})$$

**Cosine Benzerliği:**
$$\text{sim}(u, v) = \frac{u \cdot v}{\|u\| \|v\|} \in [-1, 1]$$


In [ ]:
sentences = [
    "Makine öğrenmesi teknolojiyi dönüştürüyor.",
    "Yapay zeka bilişimi devrim yapıyor.",
    "Dağlarda yürüyüş yapmaktan hoşlanırım."
]

print("="*80)
print("EMBEDDING BENZERLİĞİ GÖSTERİMİ")
print("="*80)

result = embedding(model=EMBEDDING_MODEL, input=sentences)
embeddings_array = np.array([item['embedding'] for item in result.data])
print(f"\n✓ {len(sentences)} cümle için embedding oluşturuldu")
print(f"✓ Embedding boyutu: {embeddings_array.shape[1]}\n")

def cosine_similarity(v1, v2):
    return np.dot(v1, v2) / (np.linalg.norm(v1) * np.linalg.norm(v2))

print("📊 Benzerlik Matrisi:")
print("-"*80)

sim_1_2 = cosine_similarity(embeddings_array[0], embeddings_array[1])
sim_1_3 = cosine_similarity(embeddings_array[0], embeddings_array[2])

print(f"\nCümle 1: '{sentences[0]}'")
print(f"Cümle 2: '{sentences[1]}'")
print(f"Benzerlik: {sim_1_2:.4f} ← Yüksek (ikisi de YZ/ML hakkında)\n")

print(f"Cümle 1: '{sentences[0]}'")
print(f"Cümle 3: '{sentences[2]}'")
print(f"Benzerlik: {sim_1_3:.4f} ← Düşük (farklı konular)\n")

print("="*80)
print("\n💡 Embedding'ler semantik anlamı yakalar, sadece kelime eşleşmesini değil.")
print("="*80)


### 2.2 RAG Mimarisi: Retrieval ile Generation'ı Güçlendirme

**RAG Pipeline:**
1. **İndeksleme (Offline):** $\{d_1, ..., d_N\} \xrightarrow{\phi} \{v_1, ..., v_N\}$ (dokümanlar → embedding'ler)
2. **Retrieval (Online):** $q \xrightarrow{\phi} v_q$, en benzer $D_{top-k} = \text{TopK}(\text{sim}(v_q, v_i))$'yi bul
3. **Generation:** $\text{LLM}(q, D_{top-k}) \to \text{cevap}$


In [ ]:
class SemanticSearchEngine:
    def __init__(self, embedding_model: str = EMBEDDING_MODEL, embedding_dim: int = EMBEDDING_DIM):
        self.model = embedding_model
        self.dim = embedding_dim
        self.documents: List[str] = []
        self.document_embeddings: Optional[np.ndarray] = None
        self.metadata: List[Dict] = []

    def _embed_texts(self, texts: List[str]) -> np.ndarray:
        result = embedding(model=self.model, input=texts)
        embeddings_list = [item['embedding'] for item in result.data]
        return np.array(embeddings_list)

    def index_documents(self, documents: List[str], metadata: Optional[List[Dict]] = None) -> None:
        print(f"{len(documents)} doküman indeksleniyor...")
        self.documents = documents
        self.document_embeddings = self._embed_texts(documents)
        self.metadata = metadata if metadata else [{}] * len(documents)
        print(f"✓ {len(documents)} doküman indekslendi")
        print(f"✓ İndeks boyutu: {self.document_embeddings.nbytes / 1024:.2f} KB")

    def search(self, query: str, top_k: int = 3, return_scores: bool = True) -> List[Dict]:
        if self.document_embeddings is None:
            raise ValueError("Hiç doküman indekslenmemiş. Önce index_documents() çağırın.")

        query_embedding = self._embed_texts([query])[0]
        similarities = np.dot(self.document_embeddings, query_embedding)
        top_k_indices = np.argsort(similarities)[::-1][:top_k]

        results = []
        for idx in top_k_indices:
            result = {
                'document': self.documents[idx],
                'metadata': self.metadata[idx],
            }
            if return_scores:
                result['score'] = float(similarities[idx])
            results.append(result)
        return results

Embedding'ler kullanarak production semantik arama.

    İlgiyi ayırır:
    - İndeksleme: Tek seferlik embedding üretimi
    - Sorgu: Hızlı benzerlik hesaplaması


In [ ]:
def __init__(self, embedding_model: str = EMBEDDING_MODEL, embedding_dim: int = EMBEDDING_DIM):
        self.model = embedding_model
        self.dim = embedding_dim
        self.documents: List[str] = []
        self.document_embeddings: Optional[np.ndarray] = None
        self.metadata: List[Dict] = []

def _embed_texts(self, texts: List[str]) -> np.ndarray:
        result = embedding(model=self.model, input=texts)
        embeddings_list = [item['embedding'] for item in result.data]
        return np.array(embeddings_list)

def index_documents(self, documents: List[str], metadata: Optional[List[Dict]] = None) -> None:
        print(f"{len(documents)} doküman indeksleniyor...")
        self.documents = documents
        self.document_embeddings = self._embed_texts(documents)
        self.metadata = metadata if metadata else [{}] * len(documents)
        print(f"✓ {len(documents)} doküman indekslendi")
        print(f"✓ İndeks boyutu: {self.document_embeddings.nbytes / 1024:.2f} KB")

def search(self, query: str, top_k: int = 3, return_scores: bool = True) -> List[Dict]:
        if self.document_embeddings is None:
            raise ValueError("Hiç doküman indekslenmemiş. Önce index_documents() çağırın.")

        query_embedding = self._embed_texts([query])[0]
        similarities = np.dot(self.document_embeddings, query_embedding)
        top_k_indices = np.argsort(similarities)[::-1][:top_k]

        results = []
        for idx in top_k_indices:
            result = {
                'document': self.documents[idx],
                'metadata': self.metadata[idx],
            }
            if return_scores:
                result['score'] = float(similarities[idx])
            results.append(result)
        return results

print("✓ SemanticSearchEngine sınıfı tanımlandı")


### RAG Sistemi

Tam RAG pipeline: retrieval + generation + kaynak atıfı + hata yönetimi.


In [ ]:
class ProductionRAGSystem:
    def __init__(
        self,
        embedding_model: str = EMBEDDING_MODEL,
        generative_model: str = DEFAULT_MODEL,
        embedding_dim: int = EMBEDDING_DIM
    ):
        self.generative_model = generative_model
        self.search_engine = SemanticSearchEngine(embedding_model, embedding_dim)
        self.query_count = 0

    def index_knowledge_base(self, documents: List[str], metadata: Optional[List[Dict]] = None) -> None:
        self.search_engine.index_documents(documents, metadata)
        print(f"✓ Bilgi tabanı {len(documents)} doküman ile hazır")

    def generate_answer(self, query: str, retrieved_docs: List[Dict], max_context_length: int = 2000) -> Dict:
        context_parts = []
        sources = []

        for i, doc in enumerate(retrieved_docs[:5], 1):
            context_parts.append(f"[Doküman {i}]\n{doc['document']}")
            sources.append({
                'document': doc['document'],
                'metadata': doc['metadata'],
                'relevance_score': doc.get('score', 0.0)
            })

        context = "\n\n".join(context_parts)

        if len(context) > max_context_length * 4:
            context = context[:max_context_length * 4] + "\n\n[... bağlam kesildi ...]"

        rag_prompt = f"""Sen yardımsever bir YZ asistanısın. Kullanıcının sorusunu SADECE aşağıdaki bağlamdaki bilgileri kullanarak cevapla.

KURALLAR:
1. Cevabını tamamen sağlanan bağlama dayandır
2. Bağlamda yeterli bilgi yoksa bunu açıkça belirt
3. Hangi doküman(lar)ı kullandığını belirt (örn: "Doküman 2'ye göre...")
4. Kısa ama kapsamlı ol

Bağlam:
{context}

Kullanıcı Sorusu: {query}

Cevap:"""

        try:
            answer = call_llm(
                [{"role": "user", "content": rag_prompt}],
                model=self.generative_model,
                temperature=0.3,
                max_tokens=500
            )
            success = True
            error = None
        except Exception as e:
            answer = f"Cevap oluşturma hatası: {str(e)}"
            success = False
            error = str(e)

        return {
            'answer': answer,
            'sources': sources,
            'query': query,
            'success': success,
            'error': error
        }

    def query(self, query: str, top_k: int = 3, return_sources: bool = True, verbose: bool = True) -> Dict:
        self.query_count += 1

        if verbose:
            print(f"\n{'='*80}")
            print(f"Sorgu #{self.query_count}: {query}")
            print('='*80)

        retrieved = self.search_engine.search(query, top_k=top_k, return_scores=True)

        if verbose:
            print(f"\n✓ {len(retrieved)} doküman alındı")

        result = self.generate_answer(query, retrieved)

        if verbose:
            print(f"\n📝 Cevap:\n{result['answer']}")
            if return_sources:
                print(f"\n📚 Kaynaklar:")
                for i, src in enumerate(result['sources'], 1):
                    print(f"  [{i}] {src['document'][:60]}... (skor: {src['relevance_score']:.3f})")

        if not return_sources:
            del result['sources']

        return result

Tam RAG sistemi: Retrieval + Generation.


In [ ]:
def __init__(
        self,
        embedding_model: str = EMBEDDING_MODEL,
        generative_model: str = DEFAULT_MODEL,
        embedding_dim: int = EMBEDDING_DIM
    ):
        self.generative_model = generative_model
        self.search_engine = SemanticSearchEngine(embedding_model, embedding_dim)
        self.query_count = 0

def index_knowledge_base(self, documents: List[str], metadata: Optional[List[Dict]] = None) -> None:
        self.search_engine.index_documents(documents, metadata)
        print(f"✓ Bilgi tabanı {len(documents)} doküman ile hazır")

def generate_answer(self, query: str, retrieved_docs: List[Dict], max_context_length: int = 2000) -> Dict:
        context_parts = []
        sources = []

        for i, doc in enumerate(retrieved_docs[:5], 1):
            context_parts.append(f"[Doküman {i}]\n{doc['document']}")
            sources.append({
                'document': doc['document'],
                'metadata': doc['metadata'],
                'relevance_score': doc.get('score', 0.0)
            })

        context = "\n\n".join(context_parts)

        if len(context) > max_context_length * 4:
            context = context[:max_context_length * 4] + "\n\n[... bağlam kesildi ...]"

        rag_prompt = f


Sen yardımsever bir YZ asistanısın. Kullanıcının sorusunu SADECE aşağıdaki bağlamdaki bilgileri kullanarak cevapla.

KURALLAR:
1. Cevabını tamamen sağlanan bağlama dayandır
2. Bağlamda yeterli bilgi yoksa bunu açıkça belirt
3. Hangi doküman(lar)ı kullandığını belirt (örn: "Doküman 2'ye göre...")
4. Kısa ama kapsamlı ol

Bağlam:
{context}

Kullanıcı Sorusu: {query}

Cevap:


In [ ]:
def generate_answer(self, query: str, retrieved_docs: List[Dict], max_context_length: int = 2000) -> Dict:
        context_parts = []
        sources = []

        for i, doc in enumerate(retrieved_docs[:5], 1):
            context_parts.append(f"[Doküman {i}]\n{doc['document']}")
            sources.append({
                'document': doc['document'],
                'metadata': doc['metadata'],
                'relevance_score': doc.get('score', 0.0)
            })

        context = "\n\n".join(context_parts)

        if len(context) > max_context_length * 4:
            context = context[:max_context_length * 4] + "\n\n[... bağlam kesildi ...]"

        rag_prompt = f"""Sen yardımsever bir YZ asistanısın. Kullanıcının sorusunu SADECE aşağıdaki bağlamdaki bilgileri kullanarak cevapla.\n\nKURALLAR:\n1. Cevabını tamamen sağlanan bağlama dayandır\n2. Bağlamda yeterli bilgi yoksa bunu açıkça belirt\n3. Hangi doküman(lar)ı kullandığını belirt (örn: "Doküman 2'ye göre...")\n4. Kısa ama kapsamlı ol\n\nBağlam:\n{context}\n\nKullanıcı Sorusu: {query}\n\nCevap:"""

        try:
            answer = call_llm(
                [{"role": "user", "content": rag_prompt}],
                model=self.generative_model,
                temperature=0.3,
                max_tokens=500
            )
            success = True
            error = None
        except Exception as e:
            answer = f"Cevap oluşturma hatası: {str(e)}"
            success = False
            error = str(e)

        return {
            'answer': answer,
            'sources': sources,
            'query': query,
            'success': success,
            'error': error
        }

In [ ]:
def query(self, query: str, top_k: int = 3, return_sources: bool = True, verbose: bool = True) -> Dict:
        self.query_count += 1

        if verbose:
            print(f"\n{'='*80}")
            print(f"Sorgu #{self.query_count}: {query}")
            print('='*80)

        retrieved = self.search_engine.search(query, top_k=top_k, return_scores=True)

        if verbose:
            print(f"\n✓ {len(retrieved)} doküman alındı")

        result = self.generate_answer(query, retrieved)

        if verbose:
            print(f"\n📝 Cevap:\n{result['answer']}")
            if return_sources:
                print(f"\n📚 Kaynaklar:")
                for i, src in enumerate(result['sources'], 1):
                    print(f"  [{i}] {src['document'][:60]}... (skor: {src['relevance_score']:.3f})")

        if not return_sources:
            del result['sources']

        return result

print("✓ 'query' metodu tanımlandı")

### RAG Sistemi Demosu

Örnek bilgi tabanı oluşturup test sorguları çalıştıralım.


In [ ]:
documents = [
    "Makine öğrenmesi, açık programlama olmadan veriden öğrenen bir YZ alt kümesidir.",
    "Derin öğrenme, hiyerarşik temsiller öğrenmek için çok katmanlı sinir ağları kullanır.",
    "Transfer öğrenme, yeni görevleri verimli şekilde çözmek için önceden eğitilmiş modelleri kullanır.",
    "Pekiştirmeli öğrenme, ödül sinyalleri ile deneme-yanılma yoluyla ajanları eğitir.",
    "GPT ve Gemini gibi büyük dil modelleri insan benzeri metin anlayıp üretebilir.",
    "Embedding'ler, kelimeleri veya dokümanları sürekli uzayda yoğun vektörler olarak temsil eder.",
    "Retrieval-augmented generation, bilgi alımı ile metin üretimini birleştirir.",
]

metadata = [
    {"category": "ML Temelleri", "zorluk": "başlangıç"},
    {"category": "Derin Öğrenme", "zorluk": "orta"},
    {"category": "Transfer Öğrenme", "zorluk": "orta"},
    {"category": "RL", "zorluk": "ileri"},
    {"category": "LLM'ler", "zorluk": "ileri"},
    {"category": "Embedding'ler", "zorluk": "orta"},
    {"category": "RAG", "zorluk": "ileri"},
]

rag_system = ProductionRAGSystem()
rag_system.index_knowledge_base(documents, metadata)

print("\n" + "="*80)
print("RAG SİSTEMİ GÖSTERİMİ")
print("="*80)

test_query = "Önceden eğitilmiş modelleri yeni bir görev için nasıl kullanabilirim?"
result = rag_system.query(test_query, top_k=3)

print("\n" + "="*80)
print("\n💡 RAG, LLM'lerin harici bilgiye dinamik erişimini sağlar.")
print("="*80)


---

## Faz 3: Deterministik Arayüz

Şimdi LLM'i function calling yoluyla deterministik araçlarla donatıyoruz.

### 3.1 Function Calling: Stokastikten Deterministiğe

**Zorluk:** LLM'ler olasılıksaldır ve halüsinasyon yapabilir.  
**Çözüm:** Belirli görevler için deterministik araçlar sağla.

**Mimari:**
1. **Araç Bildirimi:** Mevcut fonksiyonları tanımlayan JSON şema
2. **Araç Seçimi:** LLM hangi aracı hangi parametrelerle kullanacağına karar verir
3. **Araç Çalıştırma:** Sistem fonksiyonu deterministik şekilde çalıştırır
4. **Sonuç Entegrasyonu:** LLM araç çıktısını doğal dile sentezler

### Araç İmplementasyonları

Üç temel deterministik fonksiyon tanımlıyoruz: hava durumu, hesaplama ve bilgi tabanı araması.


In [ ]:
def get_current_weather(location: str, unit: str = "celsius") -> str:
    weather_db = {
        "istanbul": {"temp_c": 18, "condition": "Parçalı bulutlu", "humidity": 72},
        "ankara": {"temp_c": 12, "condition": "Güneşli", "humidity": 45},
        "izmir": {"temp_c": 22, "condition": "Açık", "humidity": 68},
        "antalya": {"temp_c": 25, "condition": "Güneşli", "humidity": 55}
    }

    location_key = location.lower().replace("ı", "i")
    data = weather_db.get(location_key, {"temp_c": 20, "condition": "Bilinmiyor", "humidity": 50})

    temp = data["temp_c"]
    if unit == "fahrenheit":
        temp = (temp * 9/5) + 32

    return json.dumps({
        "location": location,
        "temperature": temp,
        "unit": unit,
        "condition": data["condition"],
        "humidity": data["humidity"]
    })

Bir konum için güncel hava durumunu al.


In [ ]:
def calculate(expression: str) -> str:
    try:
        allowed_chars = set("0123456789+-*/(). ")
        if not all(c in allowed_chars for c in expression):
            return json.dumps({"error": "Geçersiz karakterler tespit edildi"})

        result = eval(expression)
        return json.dumps({"expression": expression, "result": result})
    except Exception as e:
        return json.dumps({"error": f"Hesaplama hatası: {str(e)}"})

Matematiksel ifadeyi güvenli şekilde değerlendir.


In [ ]:
def search_knowledge_base(query: str) -> str:
    mock_results = [
        "Transfer öğrenme, yeni görevler için önceden eğitilmiş modelleri kullanmaya izin verir.",
        "Fine-tuning, önceden eğitilmiş bir modeli belirli bir alana adapte eder."
    ]

    return json.dumps({
        "query": query,
        "results": mock_results
    })

RAG bilgi tabanında ara.


In [ ]:
print("✓ Araç fonksiyonları tanımlandı:")
print("  - get_current_weather()")
print("  - calculate()")
print("  - search_knowledge_base()")

### Araç Kaydı (Tool Registry)

JSON Schema bildirimleri + Python fonksiyon eşleştirmesi.


In [ ]:
tools = [
    {
        "type": "function",
        "function": {
            "name": "get_current_weather",
            "description": "Belirli bir konum için güncel hava durumunu al",
            "parameters": {
                "type": "object",
                "properties": {
                    "location": {
                        "type": "string",
                        "description": "Şehir adı, örn: Istanbul, Ankara, Izmir"
                    },
                    "unit": {
                        "type": "string",
                        "enum": ["celsius", "fahrenheit"],
                        "description": "Sıcaklık birimi"
                    }
                },
                "required": ["location"]
            }
        }
    },
    {
        "type": "function",
        "function": {
            "name": "calculate",
            "description": "Matematiksel ifadeyi değerlendir",
            "parameters": {
                "type": "object",
                "properties": {
                    "expression": {
                        "type": "string",
                        "description": "Matematiksel ifade, örn: '25 * 3', '100 / 4'"
                    }
                },
                "required": ["expression"]
            }
        }
    },
    {
        "type": "function",
        "function": {
            "name": "search_knowledge_base",
            "description": "Bilgi tabanında bilgi ara",
            "parameters": {
                "type": "object",
                "properties": {
                    "query": {
                        "type": "string",
                        "description": "Arama sorgusu veya soru"
                    }
                },
                "required": ["query"]
            }
        }
    }
]

tool_functions = {
    "get_current_weather": get_current_weather,
    "calculate": calculate,
    "search_knowledge_base": search_knowledge_base
}

print("✓ Araç kaydı yapılandırıldı")
print(f"  Mevcut araçlar: {list(tool_functions.keys())}")


---

## Faz 4: Otonom Döngü

Şimdi ajanı oluşturuyoruz: hangi araçları ne zaman kullanacağı hakkında akıl yürüten otonom bir sistem.

### 4.1 ReAct Kalıbı

**ReAct = Reasoning (Akıl Yürütme) + Acting (Eylem)**

Ajan döngüsü:
```
while not done:
    1. Akıl Yürüt: LLM durumu analiz eder
    2. Eyleme Geç: LLM araç ve parametreleri seçer
    3. Gözlemle: Sistem aracı çalıştırır, sonuç döner
    4. Güncelle: Gözlemi bağlama ekle
```


In [ ]:
def run_agent(
    user_query: str,
    model: str = DEFAULT_MODEL,
    max_iterations: int = 5,
    verbose: bool = True
) -> str:
    if verbose:
        print("="*80)
        print("🤖 AJAN BAŞLADI")
        print("="*80)
        print(f"📥 Kullanıcı Sorgusu: {user_query}\n")

    messages = [{"role": "user", "content": user_query}]

    for iteration in range(1, max_iterations + 1):
        if verbose:
            print(f"\n{'─'*80}")
            print(f"🔄 İTERASYON {iteration}")
            print(f"{'─'*80}")

        try:
            response = completion(
                model=model,
                messages=messages,
                tools=tools,
                temperature=0.1
            )

            response_message = response.choices[0].message
            tool_calls = getattr(response_message, 'tool_calls', None)

            if not tool_calls:
                final_answer = response_message.content
                if verbose:
                    print(f"\n✅ FİNAL CEVAP:\n{final_answer}")
                    print("="*80)
                return final_answer

            if verbose:
                print(f"\n🔧 Model {len(tool_calls)} araç çağrısı istiyor:\n")

            messages.append(response_message)

            for tool_call in tool_calls:
                function_name = tool_call.function.name
                function_args = json.loads(tool_call.function.arguments)

                if verbose:
                    print(f"   📞 Fonksiyon: {function_name}()")
                    print(f"      Argümanlar: {json.dumps(function_args, ensure_ascii=False, indent=10)}")

                function_to_call = tool_functions[function_name]
                function_response = function_to_call(**function_args)

                if verbose:
                    print(f"      ✅ Sonuç: {function_response}\n")

                messages.append({
                    "role": "tool",
                    "tool_call_id": tool_call.id,
                    "name": function_name,
                    "content": function_response
                })

        except Exception as e:
            error_msg = f"❌ Hata: {str(e)}"
            if verbose:
                print(error_msg)
            return error_msg

    return "⚠️ Maksimum iterasyona ulaşıldı, final cevap yok."

Function calling ile otonom ajan çalıştır.


In [ ]:
print("✓ Ajan sistemi hazır")

### 4.2 Ajan Gösterimleri

Ajanı giderek karmaşık görevlerde test ediyoruz.


In [ ]:
print("\n" + "="*80)
print("DEMO 1: BASİT ARAÇ KULLANIMI")
print("="*80)

result1 = run_agent("Istanbul'da hava nasıl?")
print("\n" + "="*80)

print("\n" + "="*80)
print("DEMO 2: ÇOKLU ARAÇ KOORDİNASYONU")
print("="*80)

result2 = run_agent(
    "Istanbul ve Ankara arasındaki sıcaklık farkı nedir? Hesapla."
)
print("\n" + "="*80)

print("\n" + "="*80)
print("DEMO 3: RAG + FUNCTION CALLING")
print("="*80)

result3 = run_agent(
    "Bilgi tabanında transfer öğrenme hakkında ara, sonra bunun hava tahmini ile ilişkisini anlat."
)
print("\n" + "="*80)


---

## Final Gösteri: Karmaşık Çoklu Araç Sorgusu

Şimdi tam sistemi şunları gerektiren karmaşık bir görevde gösteriyoruz:
1. Bilgi alımı (RAG)
2. Gerçek zamanlı veri çekme (hava durumu API)
3. Matematiksel hesaplama (hesap makinesi)
4. Çok adımlı akıl yürütme


In [ ]:
complex_query = "Ankara'daki sıcaklığı kontrol et. Eğer 15°C'nin altındaysa, bilgi tabanından transfer öğrenme hakkında bilgi ver. Son olarak, Ankara'nın şu anki sıcaklığından %20 daha yüksek olan sıcaklığı hesapla."

İşte karmaşık bir görev:
1. Ankara'daki sıcaklığı kontrol et
2. Eğer 15°C'nin altındaysa, bilgi tabanından transfer öğrenme hakkında bilgi ver
3. Ankara'nın şu anki sıcaklığından %20 daha yüksek olan sıcaklığı hesapla


In [ ]:
print("\n" + "="*80)
print("FİNAL GÖSTERİMİ: TAM SİSTEM")
print("="*80)
print(f"\nKarmaşık Sorgu:\n{complex_query}")
print("\n" + "="*80)

final_result = run_agent(complex_query, verbose=True)

print("\n" + "="*80)
print("\n🎉 GÖSTERİM TAMAMLANDI")
print("="*80)
print("\n💡 Anahtar Başarılar:")
print("   ✓ Faz 0: Sağlam API yönetimi ile birleşik ortam")
print("   ✓ Faz 1: Prompt mühendisliği ile stokastik operatörler")
print("   ✓ Faz 2: Production RAG ile semantik uzay")
print("   ✓ Faz 3: Function calling ile deterministik arayüzler")
print("   ✓ Faz 4: Çoklu araç koordinasyonu ile otonom ajan döngüsü")
print("\n📚 Bu notebook tam mimariyi gösteriyor:")
print("   Temel LLM çağrılarından → RAG + Araçlar ile otonom ajanlara")
print("="*80)
